- This notebook generates the dot plot showing the DEG between all cell types at the group level.

In [1]:
from sklearn.neighbors import NearestNeighbors
import numpy as np
from tqdm import tqdm
import anndata
import pandas as pd
import scanpy as sc

#### 1. Load in the data

In [ ]:
%%time

# load 1311 posterior 
Donor_1311_posterior_adata  = anndata.read_h5ad(r'./../../MERFISH_adata_QC/mapmycell_annotated_adata/MER2_Gpe_Gpi_CaPu_1311__MERFISH_annotated.h5ad')
spatialModuleAnnotation = pd.read_csv(r'./../..spatialDomain_analysis/processed_data/donor_1311_PosteriorMERFISH/GroupLevelspatialModule_MatrixStriosome_included_cleaned_final.csv', index_col=0)
Donor_1311_posterior_adata.obs = Donor_1311_posterior_adata.obs.join(spatialModuleAnnotation[['Final_Major_region_label','MatrixStriosome_label']])


print('load 1311 posterior .....')


# # load 2427 posterior 
Donor_2427_posterior_adata = anndata.read_h5ad(r'./../../MERFISH_adata_QC/mapmycell_annotated_adata/MER4_Gpe_Gpi_2724__MERFISH_annotated.h5ad')
spatialModuleAnnotation = pd.read_csv(r'./../../spatialDomain_analysis/processed_data/donor_2724_PosteriorMERFISH/GroupLevelspatialModule_MatrixStriosome_included_cleaned_final.csv', index_col=0)
Donor_2427_posterior_adata.obs = Donor_2427_posterior_adata.obs.join(spatialModuleAnnotation[['Final_Major_region_label','MatrixStriosome_label']])
print('load 2427 posterior .....')


# # load 2427 anterior 
Donor_2427_anterior_adata = anndata.read_h5ad(r'./../../MERFISH_adata_QC/mapmycell_annotated_adata/MER1_CaPuNAC_2427__MERFISH_annotated.h5ad')
spatialModuleAnnotation = pd.read_csv(r'./../../spatialDomain_analysis/processed_data/chip5_AnteriorMERFISH/GroupLevelspatialModule_MatrixStriosome_included_cleaned_final.csv', index_col=0)
Donor_2427_anterior_adata.obs = Donor_2427_anterior_adata.obs.join(spatialModuleAnnotation[['Final_Major_region_label','MatrixStriosome_label']])
print('load 2427 anterior .....')


# # load 3924 anterior 
Donor_3924_anterior_adata = anndata.read_h5ad(r'./../../MERFISH_adata_QC/mapmycell_annotated_adata/MER5_CaPuNAc_3924__MERFISH_annotated.h5ad')
spatialModuleAnnotation = pd.read_csv(r'./../../spatialDomain_analysis/processed_data/donor_3924_AnteriorMERFISH/GroupLevelspatialModule_MatrixStriosome_included_cleaned_final.csv', index_col=0)
Donor_3924_anterior_adata.obs = Donor_3924_anterior_adata.obs.join(spatialModuleAnnotation[['Final_Major_region_label','MatrixStriosome_label']])
print('load 3924 anterior  .....')

load 1311 posterior .....
load 2427 posterior .....
load 2427 anterior .....
load 3924 anterior  .....
CPU times: user 1min 28s, sys: 16.4 s, total: 1min 44s
Wall time: 1min 45s


- Concatenate the anndata

- Make sure the same order of genes is used in all samples

In [3]:
# make sure the same order of genes is used in all samples  and replace count with raw counts
common_gns = np.array(Donor_2427_posterior_adata.var_names)
Donor_1311_posterior_adata.X = Donor_1311_posterior_adata.layers['X_raw']
Donor_1311_posterior_adata = Donor_1311_posterior_adata[:,common_gns].copy()
Donor_1311_posterior_adata.obsm['X_spatial'] = Donor_1311_posterior_adata.obsm['X_spatial_rotated'] if 'X_spatial_rotated'  in Donor_1311_posterior_adata.obsm else Donor_1311_posterior_adata.obsm['X_spatial']

Donor_2427_posterior_adata.X = Donor_2427_posterior_adata.layers['X_raw']
Donor_2427_posterior_adata = Donor_2427_posterior_adata[:,common_gns].copy()
Donor_2427_posterior_adata.obsm['X_spatial'] = Donor_2427_posterior_adata.obsm['X_spatial_rotated'] if 'X_spatial_rotated'  in Donor_2427_posterior_adata.obsm else Donor_2427_posterior_adata.obsm['X_spatial']

Donor_2427_anterior_adata.X = Donor_2427_anterior_adata.obsm['X_raw']
Donor_2427_anterior_adata = Donor_2427_anterior_adata[:,common_gns].copy()
Donor_2427_anterior_adata.obsm['X_spatial'] = Donor_2427_anterior_adata.obsm['X_spatial_rotated'] if 'X_spatial_rotated'  in Donor_2427_anterior_adata.obsm else Donor_2427_anterior_adata.obsm['X_spatial']

Donor_3924_anterior_adata.X = Donor_3924_anterior_adata.layers['X_raw']
Donor_3924_anterior_adata = Donor_3924_anterior_adata[:,common_gns].copy()
Donor_3924_anterior_adata.obsm['X_spatial'] = Donor_3924_anterior_adata.obsm['X_spatial_rotated'] if 'X_spatial_rotated'  in Donor_3924_anterior_adata.obsm else Donor_3924_anterior_adata.obsm['X_spatial']

In [5]:
# concatenate the data
adata = anndata.concat([Donor_1311_posterior_adata,Donor_2427_posterior_adata,Donor_2427_anterior_adata,Donor_3924_anterior_adata],
                       label = 'samples',
                        keys= ['Donor_1311_posterior','Donor_2724_posterior','Donor_2724_anterior','Donor_3924_anterior'],
                        fill_value=0,
                        join='outer',
                        merge='same' ,
                        index_unique='_' # make the cell index unique
                        ) 

In [6]:
adata

AnnData object with n_obs × n_vars = 3250780 × 673
    obs: 'volm', 'n_genes_by_counts', 'log1p_n_genes_by_counts', 'total_counts', 'log1p_total_counts', 'pct_counts_in_top_50_genes', 'pct_counts_in_top_100_genes', 'pct_counts_in_top_200_genes', 'pct_counts_in_top_500_genes', 'leiden', 'Neighborhood_label', 'Neighborhood_name', 'Neighborhood_bootstrapping_probability', 'Class_label', 'Class_name', 'Class_bootstrapping_probability', 'Subclass_label', 'Subclass_name', 'Subclass_bootstrapping_probability', 'Group_label', 'Group_name', 'Group_bootstrapping_probability', 'Cluster_label', 'Cluster_name', 'Cluster_alias', 'Cluster_bootstrapping_probability', 'Final_Major_region_label', 'MatrixStriosome_label', 'samples'
    obsm: 'X_raw', 'X_spatial', 'X_spatial_rotated', 'X_umap', 'X_pca'
    layers: 'X_raw'

In [7]:
adata.X = adata.layers['X_raw'].copy()

### 2.  QC based on Volume  and Count

In [8]:
# Remove AC terms concatenated from previous data 
for col in ['n_genes_by_counts', 'log1p_n_genes_by_counts', 'total_counts', 'log1p_total_counts', 'pct_counts_in_top_50_genes', 'pct_counts_in_top_100_genes', 'pct_counts_in_top_200_genes', 'pct_counts_in_top_500_genes']:
    del adata.obs[col]

In [9]:
# Calculate qc metrics 
sc.pp.calculate_qc_metrics(adata,inplace=True)

# QC by count 
totalct_1pp = np.percentile(adata.obs['total_counts'], 1)
totalct_99pp = np.percentile(adata.obs['total_counts'], 99)
totalct_cond = (adata.obs['total_counts'] > totalct_1pp) & (adata.obs['total_counts'] < totalct_99pp)
# QC by volume
Vol_1pp = np.percentile(adata.obs['volm'], 1)
Vol_99pp = np.percentile(adata.obs['volm'], 99)
vol_cond = (adata.obs['volm'] > Vol_1pp) & (adata.obs['volm'] < Vol_99pp)
adata = adata[vol_cond & totalct_cond].copy()
adata

/home/exx/anaconda3/envs/3D_Hippo_MERFISH_env/lib/python3.10/site-packages/scanpy/preprocessing/_qc.py:432: RuntimeWarning: invalid value encountered in divide
  return values / sums[:, None]


AnnData object with n_obs × n_vars = 2525172 × 673
    obs: 'volm', 'leiden', 'Neighborhood_label', 'Neighborhood_name', 'Neighborhood_bootstrapping_probability', 'Class_label', 'Class_name', 'Class_bootstrapping_probability', 'Subclass_label', 'Subclass_name', 'Subclass_bootstrapping_probability', 'Group_label', 'Group_name', 'Group_bootstrapping_probability', 'Cluster_label', 'Cluster_name', 'Cluster_alias', 'Cluster_bootstrapping_probability', 'Final_Major_region_label', 'MatrixStriosome_label', 'samples', 'n_genes_by_counts', 'log1p_n_genes_by_counts', 'total_counts', 'log1p_total_counts', 'pct_counts_in_top_50_genes', 'pct_counts_in_top_100_genes', 'pct_counts_in_top_200_genes', 'pct_counts_in_top_500_genes'
    var: 'n_cells_by_counts', 'mean_counts', 'log1p_mean_counts', 'pct_dropout_by_counts', 'total_counts', 'log1p_total_counts'
    obsm: 'X_raw', 'X_spatial', 'X_spatial_rotated', 'X_umap', 'X_pca'
    layers: 'X_raw'

#### 3. Normalize 

In [10]:
med_volm = np.median(adata.obs['volm'])
temp = adata.X.astype('float').copy()
temp /= adata.obs['volm'].values[:,np.newaxis]
temp *= med_volm
adata.X  = temp

In [11]:
target_sum  = np.median(np.array(adata.X.sum(axis=-1)))
sc.pp.normalize_total(adata, target_sum=target_sum)
sc.pp.log1p(adata)
# keep record of the log-normalized counts
adata.layers['log_count'] =  adata.X.copy()

#### 4. Run DEG 

In [11]:
adata

AnnData object with n_obs × n_vars = 2525172 × 673
    obs: 'volm', 'leiden', 'Neighborhood_label', 'Neighborhood_name', 'Neighborhood_bootstrapping_probability', 'Class_label', 'Class_name', 'Class_bootstrapping_probability', 'Subclass_label', 'Subclass_name', 'Subclass_bootstrapping_probability', 'Group_label', 'Group_name', 'Group_bootstrapping_probability', 'Cluster_label', 'Cluster_name', 'Cluster_alias', 'Cluster_bootstrapping_probability', 'Final_Major_region_label', 'MatrixStriosome_label', 'samples', 'n_genes_by_counts', 'log1p_n_genes_by_counts', 'total_counts', 'log1p_total_counts', 'pct_counts_in_top_50_genes', 'pct_counts_in_top_100_genes', 'pct_counts_in_top_200_genes', 'pct_counts_in_top_500_genes'
    var: 'n_cells_by_counts', 'mean_counts', 'log1p_mean_counts', 'pct_dropout_by_counts', 'total_counts', 'log1p_total_counts'
    uns: 'log1p'
    obsm: 'X_raw', 'X_spatial', 'X_spatial_rotated', 'X_umap', 'X_pca'
    layers: 'X_raw', 'log_count'

In [13]:
def sort_Gene_plus_adata(subadata, class_order):
    # select top ten marker genes from each class. 
    from tqdm import tqdm
    markers = {}
    group_names = np.unique(subadata.obs['Group_name'])
    for group_ in tqdm(group_names, desc = 'get top 20 marker genes'):
        df = sc.get.rank_genes_groups_df(subadata, group_)
        df = df[(df.pvals_adj < 0.05) & (df.logfoldchanges > 1)]
        markers[group_] = list(df.iloc[:7,:]['names'].values)

    # keep unique genes 
    markers_unq = np.unique([gn for nm in markers for gn in markers[nm]] ) 
    # remove Gfap and APoe, if in the list 
    markers_unq = list(set(markers_unq).difference(['GFAP','APOE']))
    #sort the group name based on class order 
    Group_category_order = []
    for class_ in class_order:
        Group_category_order.append(np.unique(subadata[subadata.obs['Class_name'] == class_].obs['Group_name']))
    Group_category_order = np.hstack(Group_category_order)
    subadata.obs['Group_name'] = subadata.obs['Group_name'].astype(str)
    subadata.obs['Group_name'] = pd.Categorical(subadata.obs['Group_name'].values, categories=Group_category_order, ordered= True) 

    subadata.obs['Class_name'] = subadata.obs['Class_name'].astype(str)
    subadata.obs['Class_name'] = pd.Categorical(subadata.obs['Class_name'].values, categories=class_order, ordered= True) 

    # sort the genes 
    gnmax_group = {}
    for gn in markers_unq:
        df = pd.DataFrame(subadata[:,gn].X,index = subadata.obs['Group_name']).groupby(by = 'Group_name').mean()
        gnmax_group[gn] = df.index[np.argmax(df.values)]
    _,gngroup = list(zip(*gnmax_group.items()))
    # convert the class name to number and sort it 
    group_2_num = {nm:idx for idx,nm in enumerate(Group_category_order)}
    gngroup_ix = [group_2_num[nm] for nm in gngroup]
    sort_idx = np.argsort(gngroup_ix)
    markers_unq_sorted = np.array(markers_unq)[sort_idx]
    return subadata, markers_unq_sorted



In [14]:
%%time
sc.tl.rank_genes_groups(adata, groupby = 'Group_name' , layer = 'log_count', method = 'wilcoxon', use_raw = False)

CPU times: user 3min 37s, sys: 1min 45s, total: 5min 23s
Wall time: 5min 23s


/home/exx/anaconda3/envs/3D_Hippo_MERFISH_env/lib/python3.10/site-packages/scanpy/tools/_rank_genes_groups.py:429: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  self.stats[group_name, "names"] = self.var_names[global_indices]
/home/exx/anaconda3/envs/3D_Hippo_MERFISH_env/lib/python3.10/site-packages/scanpy/tools/_rank_genes_groups.py:431: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  self.stats[group_name, "scores"] = scores[global_indices]
/home/exx/anaconda3/envs/3D_Hippo_MERFISH_env/lib/python3.10/site-packages/scanpy/tools/_

#### 5. Generate the dot plot

In [15]:
#sort the group name based on class order 
class_order = ['CN LGE GABA','CN MGE GABA','CN CGE GABA','F M GABA', 'F M Glut','CN GABA-Glut','M Dopa','Cx GABA','OPC-Oligo','Astro-Epen','Vascular','Immune']
adata, marker_unq_sorted = sort_Gene_plus_adata(adata, class_order)

get top 20 marker genes: 100%|██████████| 60/60 [00:00<00:00, 109.35it/s]


In [ ]:
import matplotlib as mpl
import matplotlib.pyplot as plt
mpl.rcParams['font.size'] = 35
fig, ax = plt.subplots(1,1, dpi = 300, figsize = (50,80))
# fig = plt.Figure(dpi = 300, figsize = (50,80))


dotplot_obj = sc.pl.dotplot(adata, marker_unq_sorted, groupby='Group_name', dendrogram=False, swap_axes=True,ax = ax,dot_max=0.85, vmax = 2.55, dot_min = 0.25,mean_only_expressed = False, show = False)
bboxsz_legend  = dotplot_obj['size_legend_ax'].get_position()
dotplot_obj['size_legend_ax'].set_position([bboxsz_legend.xmin,bboxsz_legend.ymin,1.5*bboxsz_legend.width,bboxsz_legend.height])

bboxcolor_legend  = dotplot_obj['color_legend_ax'].get_position()
dotplot_obj['color_legend_ax'].set_position([bboxcolor_legend.xmin,bboxcolor_legend.ymin,1.5*bboxcolor_legend.width,bboxcolor_legend.height])

dotplot_obj['color_legend_ax'].set_xticks([0,0.5,1,1.5,2,2.5],[0,0.5,1,1.5,2,2.5])

plt.savefig(r'./figures/Figure3/supplemental/marker_gene_dot_plotGroup_level.eps',bbox_inches = 'tight')
plt.savefig(r'./figures/Figure3/supplemental/marker_gene_dot_plotGroup_level.tif',bbox_inches = 'tight')
plt.savefig(r'./figures/Figure3/supplemental/marker_gene_dot_plotGroup_level.png',bbox_inches = 'tight')
plt.show()